In [1]:
import sys, os
sys.path.append(os.path.abspath('../'))

In [2]:
# saved files testing
from src.utils.flow import *
from src.utils.flow_calculations import *
from src.utils.restoration import *
from src.utils.truncated_packet import *
from src.operations.size_perturbation_logic import *
from src.operations.timing_perturbation_logic import *
from src.operations.calculate_fitness import *

In [3]:
def apply_best_on_packets(packets, max_fitness, flow_id):

    index = max_fitness[1][2]
    #print(index)
    if index == 0:
        return packets
    
    params = max_fitness[1][1][index-1] # best technique
    #print(f'saved:{params}')
    
    if index == 1:
        #print('packet_size_nor')
        #print(f'size: {prepare_size_stats(packets, flow_id)}')
        
        return adjust_packet_size(packets, flow_id, params['direction'], 'normal', params['scaling_factor'], params['focus_point'])
        
                
    elif index == 2:
        #print('packet_size_uni')
        #print(f'size: {prepare_size_stats(packets, flow_id)}')
        return adjust_packet_size(packets, flow_id, params['direction'], 'uniform', params['scaling_factor'], params['focus_point'])
                
    elif index == 3:
        #print('packet_time_norm')
        #print(f'time: {prepare_timing_stats(packets, flow_id)}')
        return apply_time_perturbation_with_focus(packets, flow_id, 'normal', params['focus_point'], params['scaling_factor'])
                
    elif index == 4:
        #print('packet_time_uni')
        #print(f'time: {prepare_timing_stats(packets, flow_id)}')
        return apply_time_perturbation_with_focus(packets, flow_id, 'uniform', params['focus_point'], params['scaling_factor'])
        
    return packets

In [4]:
import pygad
import copy

class FlowOptimizer:
    def __init__(self, packets, model_name, flow_id, max_fitness):
        self.packets = packets
        self.model_name = model_name
        self.flow_id = flow_id
        self.ga_instance = None
        self.max_fitness = max_fitness
        
    def apply_best_solution(self):
        best_solution, best_solution_fitness, _ = self.ga_instance.best_solution()
        best_operations = self.decode_operations(best_solution)
        # Stosujemy najlepsze operacje do pakietów
        self.best_modified_packets = self.apply_operations_to_packets(best_operations, self.packets, self.flow_id)
        # Możesz zwrócić więcej informacji o najlepszym rozwiązaniu, jeśli potrzebujesz
        return self.best_modified_packets, best_solution_fitness

    def on_generation(self, ga_instance):
        current_population = ga_instance.population
        print(f"Flow ID: {self.flow_id}, Pokolenie: {ga_instance.generations_completed}")
        #print("Aktualna populacja:")
        #for solution in current_population:
        #    print(solution)
        # Tworzymy wiadomość zawierającą interesujące nas informacje
        message = f"Najlepszy wynik: {ga_instance.best_solution()[1]}\n"
        print(message)  # Wyświetlamy informacje na konsoli
        
        # Zapisujemy te same informacje do pliku
        #with open(f"progress_for_flow_{self.flow_id}.txt", "a") as file:
        #    file.write(message)
            
    def on_fitness(self, ga_instance):
        ga_instance.plot_fitness()

    def fitness_function(self, ga_instance, solution, solution_idx):
        
        fitnesses = []
        target_fitnesses = []
        
        operations = self.decode_operations(solution)
        
        modified_packets = self.packets # always check nop
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[0], op_type = 'size_norm')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        #print(sizing_stats)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[1], op_type = 'size_uni')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[2], op_type = 'time_norm')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[3], op_type = 'time_uni')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        #print(fitnesses)
        max_fitness_value = max(fitnesses)
        max_fitness_index = fitnesses.index(max_fitness_value)
        #print(max_fitness_index)

        max_fitness_target = target_fitnesses[max_fitness_index]

        
        # Zapisz maksymalną wartość fitness i indeks, jeśli jest większa niż obecnie zapisana maksymalna wartość
        print(self.max_fitness)
        if max_fitness_value > self.max_fitness[0][0]:
            #print(f'CONDITION max: {max_fitness_value}, prev: {self.max_fitness[0]}')
            self.max_fitness = [[max_fitness_value, max_fitness_target], self.decode_operations(solution), max_fitness_index]
            #print(f'self:{self.max_fitness[0]}')
        
        #print(max_fitness_value)
        #print(f'solution:{solution}')
        #print(f'finresses: {fitnesses}, solution:{self.decode_operations(solution)}')
        
        return max_fitness_value

    def optimize_for_flow(self):
        
        #with open(f"progress_for_flow_{self.flow_id}.txt", "w") as file:
        #    file.write("")  # Tylko czyszczenie zawartości pliku
            
        ga_instance = pygad.GA(num_generations=3,
                               num_parents_mating=1,
                               fitness_func=self.fitness_function,
                               sol_per_pop=4,                          
                               mutation_probability=0.6,
     #                          initial_population=np.array([
    #        [4.14645349, 9.76164109, 1.67182642, 2.09448623, 1, 0],
   #         [2.80090477, 4.24612439, 1.41426283, 1.12520895, 2, 1],
  #          [1.31962389, 1.47082939, 2.15440462, 1.3226799, 0, 2]
 #       ]),
                               on_generation=self.on_generation,
                               num_genes=6,  # Przykład, dostosuj do ilości operacji
                               gene_space = [{'low': 1.1, 'high': 5.0},  # size normal
                                             {'low': 0.25, 'high': 5.0}, # packet size uniform
                                             {'low': 1.1, 'high': 3.0}, # time normal
                                             {'low': 0.4, 'high': 2.4}, # time uniform
                                            [0,1,2],  # direction
                                            [0,1,2]]) # focus point 

        
        ga_instance.run()
        return ga_instance, self.max_fitness

    def decode_operations(self, genotype):
        operations = []
        

        focus_point_map = {0: "start", 1: "middle", 2: "end"}
        focus_point = None
        focus_point_index = genotype[5] 
        focus_point = focus_point_map.get(focus_point_index, None)  

        size_norm = {
            'scaling_factor': genotype[0],
            'direction': genotype[4],
            'focus_point': focus_point
        }
        
        size_uni = {
            'scaling_factor': genotype[1],
            'direction': genotype[4],
            'focus_point': focus_point
        }
        
        time_norm = {
            'scaling_factor': genotype[2],
            'direction': genotype[4],
            'focus_point': focus_point
        }
        
        
        time_uni = {
            'scaling_factor': genotype[3],
            'direction': genotype[4],
            'focus_point': focus_point
        }  
            
            
        
        operations = [size_norm, size_uni, time_norm, time_uni]
        return operations 
        


    def apply_operations_to_packets(self, operation, op_type):

        #packets = copy.deepcopy(self.packets) # deep copy for testing
        #print(f'size: {prepare_size_stats(self.packets, self.flow_id)}')
        #print(f'time: {prepare_timing_stats(self.packets, self.flow_id)}')


        scaling_factor = operation['scaling_factor']
        direction = operation.get('direction')
        focus_point = operation.get('focus_point')
        

        if op_type == 'size_norm':
            packets = adjust_packet_size_deepcopy(self.packets, self.flow_id, direction, 'normal', scaling_factor, focus_point)
            
            
        elif op_type == 'size_uni':
            packets = adjust_packet_size_deepcopy(self.packets, self.flow_id, direction, 'uniform', scaling_factor, focus_point)
            
        elif op_type == 'time_norm':
            packets = apply_time_perturbation_with_focus_deepcopy(self.packets, self.flow_id, 'normal', focus_point, scaling_factor)
            
        elif op_type == 'time_uni':
            #print(f'przed: {prepare_timing_stats(self.packets, self.flow_id)}')
            packets = apply_time_perturbation_with_focus_deepcopy(self.packets, self.flow_id, 'uniform', focus_point, scaling_factor)
            #print(f'po: {prepare_timing_stats(packets, self.flow_id)}')
            
        #print(packets)
        return packets
    

            
        

    #print(optimizer.best_solution())
    


In [24]:
import pygad
import copy

class FlowOptimizerTarget:
    def __init__(self, packets, model_name, flow_id, max_fitness):
        self.packets = packets
        self.model_name = model_name
        self.flow_id = flow_id
        self.ga_instance = None
        self.max_fitness = max_fitness
        
    def apply_best_solution(self):
        best_solution, best_solution_fitness, _ = self.ga_instance.best_solution()
        best_operations = self.decode_operations(best_solution)
        # Stosujemy najlepsze operacje do pakietów
        self.best_modified_packets = self.apply_operations_to_packets(best_operations, self.packets, self.flow_id)
        # Możesz zwrócić więcej informacji o najlepszym rozwiązaniu, jeśli potrzebujesz
        return self.best_modified_packets, best_solution_fitness

    def on_generation(self, ga_instance):
        current_population = ga_instance.population
        print(f"Flow ID: {self.flow_id}, Pokolenie: {ga_instance.generations_completed}")
        #print("Aktualna populacja:")
        #for solution in current_population:
        #    print(solution)
        # Tworzymy wiadomość zawierającą interesujące nas informacje
        message = f"Najlepszy wynik: {ga_instance.best_solution()[1]}\n"
        print(message)  # Wyświetlamy informacje na konsoli
        
        # Zapisujemy te same informacje do pliku
        #with open(f"progress_for_flow_{self.flow_id}.txt", "a") as file:
        #    file.write(message)
            
    def on_fitness(self, ga_instance):
        ga_instance.plot_fitness()

    def fitness_function(self, ga_instance, solution, solution_idx):
        
        fitnesses = []
        target_fitnesses = []
        
        operations = self.decode_operations(solution)
        
        modified_packets = self.packets # always check nop
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[0], op_type = 'size_norm')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        #print(sizing_stats)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[1], op_type = 'size_uni')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[2], op_type = 'time_norm')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        modified_packets = self.apply_operations_to_packets(operations[3], op_type = 'time_uni')
        sizing_stats = prepare_size_stats(modified_packets, self.flow_id)
        timing_stats = prepare_timing_stats(modified_packets, self.flow_id)
        fitnesses.append(1.0 - predict_single_flow(self.model_name, sizing_stats, timing_stats))
        target_fitnesses.append(1.0 - predict_single_flow_target(self.model_name, sizing_stats, timing_stats))
        
        #print(fitnesses)
        max_fitness_value = max(target_fitnesses)
        max_fitness_index = target_fitnesses.index(max_fitness_value)
        #print(max_fitness_index)

        max_fitness = fitnesses[max_fitness_index]

        
        # Zapisz maksymalną wartość fitness i indeks, jeśli jest większa niż obecnie zapisana maksymalna wartość
        if max_fitness_value > self.max_fitness[0][1]:
            #print(f'CONDITION max: {max_fitness_value}, prev: {self.max_fitness[0]}')
            self.max_fitness = [[max_fitness_value, max_fitness], self.decode_operations(solution), max_fitness_index]
            #print(f'self:{self.max_fitness[0]}')
        
        #print(max_fitness_value)
        #print(f'solution:{solution}')
        #print(f'finresses: {fitnesses}, solution:{self.decode_operations(solution)}')
        
        return max_fitness_value

    def optimize_for_flow(self):
        
        #with open(f"progress_for_flow_{self.flow_id}.txt", "w") as file:
        #    file.write("")  # Tylko czyszczenie zawartości pliku
            
        ga_instance = pygad.GA(num_generations=3,
                               num_parents_mating=1,
                               fitness_func=self.fitness_function,
                               sol_per_pop=4,                          
                               mutation_probability=0.6,
     #                          initial_population=np.array([
    #        [4.14645349, 9.76164109, 1.67182642, 2.09448623, 1, 0],
   #         [2.80090477, 4.24612439, 1.41426283, 1.12520895, 2, 1],
  #          [1.31962389, 1.47082939, 2.15440462, 1.3226799, 0, 2]
 #       ]),
                               on_generation=self.on_generation,
                               num_genes=6,  # Przykład, dostosuj do ilości operacji
                               gene_space = [{'low': 1.1, 'high': 5.0},  # size normal
                                             {'low': 0.25, 'high': 5.0}, # packet size uniform
                                             {'low': 1.1, 'high': 3.0}, # time normal
                                             {'low': 0.4, 'high': 2.4}, # time uniform
                                            [0,1,2],  # direction
                                            [0,1,2]]) # focus point 

        
        ga_instance.run()
        return ga_instance, self.max_fitness

    def decode_operations(self, genotype):
        operations = []
        

        focus_point_map = {0: "start", 1: "middle", 2: "end"}
        focus_point = None
        focus_point_index = genotype[5] 
        focus_point = focus_point_map.get(focus_point_index, None)  

        size_norm = {
            'scaling_factor': genotype[0],
            'direction': genotype[4],
            'focus_point': focus_point
        }
        
        size_uni = {
            'scaling_factor': genotype[1],
            'direction': genotype[4],
            'focus_point': focus_point
        }
        
        time_norm = {
            'scaling_factor': genotype[2],
            'direction': genotype[4],
            'focus_point': focus_point
        }
        
        
        time_uni = {
            'scaling_factor': genotype[3],
            'direction': genotype[4],
            'focus_point': focus_point
        }  
            
            
        
        operations = [size_norm, size_uni, time_norm, time_uni]
        return operations 
        


    def apply_operations_to_packets(self, operation, op_type):

        #packets = copy.deepcopy(self.packets) # deep copy for testing
        #print(f'size: {prepare_size_stats(self.packets, self.flow_id)}')
        #print(f'time: {prepare_timing_stats(self.packets, self.flow_id)}')


        scaling_factor = operation['scaling_factor']
        direction = operation.get('direction')
        focus_point = operation.get('focus_point')
        

        if op_type == 'size_norm':
            packets = adjust_packet_size_deepcopy(self.packets, self.flow_id, direction, 'normal', scaling_factor, focus_point)
            
            
        elif op_type == 'size_uni':
            packets = adjust_packet_size_deepcopy(self.packets, self.flow_id, direction, 'uniform', scaling_factor, focus_point)
            
        elif op_type == 'time_norm':
            packets = apply_time_perturbation_with_focus_deepcopy(self.packets, self.flow_id, 'normal', focus_point, scaling_factor)
            
        elif op_type == 'time_uni':
            #print(f'przed: {prepare_timing_stats(self.packets, self.flow_id)}')
            packets = apply_time_perturbation_with_focus_deepcopy(self.packets, self.flow_id, 'uniform', focus_point, scaling_factor)
            #print(f'po: {prepare_timing_stats(packets, self.flow_id)}')
            
        #print(packets)
        return packets
    

            
        

    #print(optimizer.best_solution())
    


In [9]:
# main

modified_pcap_path = "../data/interim/botnet-capture-20110816-donbot_perturbed.pcapng"
pcap_file_path = '../data/raw/botnet-capture-20110816-donbot.pcap'
model_name = 'botnet-capture-20110816-donbot'
# TODO: budowanie nazw

truncated_packets = create_truncated_packets_from_pcap(pcap_file_path)
truncated_packets = assign_flow_ids_to_packets(truncated_packets)
truncated_packets = undersample_flows_with_distribution(truncated_packets, 150)
optimizers = []  # Lista na instancje optymalizatorów

flow_ids = set(packet.flow_id for packet in truncated_packets)

extern = []
for flow_id in flow_ids:
    inter = []
    extern.append(inter)
    max_fitness = [[], [], 0]
    previous_max = 0
    for i in range(0, 5):
        #timing_stats = prepare_timing_stats(truncated_packets, flow_id)
        #sizing_stats = prepare_size_stats(truncated_packets,flow_id)
        #print(predict_single_flow(model_name, sizing_stats, timing_stats))
        truncated_packets_copy = copy.deepcopy(truncated_packets)
        optimizer = FlowOptimizer(truncated_packets_copy, model_name, flow_id, max_fitness[1]) 

        max_fitness = optimizer.optimize_for_flow()
        inter.append(max_fitness)
        
        #print(f'nowy: {max_fitness[1][0]} stary: {previous_max}')
        if max_fitness[1][0] > previous_max: # if highest value higher than before
            
            truncated_packets = apply_best_on_packets(truncated_packets, max_fitness, flow_id)
            #print(f'size after: {prepare_size_stats(truncated_packets, flow_id)}')
            #print(f'time after: {prepare_timing_stats(truncated_packets, flow_id)}')
            
            previous_max = max_fitness[1][0]
        
      


modify_and_write_packets_one_by_one(pcap_file_path, modified_pcap_path, truncated_packets)

Flow ID: 1, Pokolenie: 1
Najlepszy wynik: 0.17051189541033562

Flow ID: 1, Pokolenie: 2
Najlepszy wynik: 0.172480884501923

Flow ID: 1, Pokolenie: 3
Najlepszy wynik: 0.172480884501923



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 1, Pokolenie: 1
Najlepszy wynik: 0.2220046821365077

Flow ID: 1, Pokolenie: 2
Najlepszy wynik: 0.2220046821365077

Flow ID: 1, Pokolenie: 3
Najlepszy wynik: 0.2220046821365077



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 1, Pokolenie: 1
Najlepszy wynik: 0.2499796939403468

Flow ID: 1, Pokolenie: 2
Najlepszy wynik: 0.2499796939403468

Flow ID: 1, Pokolenie: 3
Najlepszy wynik: 0.2499796939403468



...

Flow ID: 2047, Pokolenie: 1
Najlepszy wynik: 0.31333906015429247

Flow ID: 2047, Pokolenie: 2
Najlepszy wynik: 0.31333906015429247

Flow ID: 2047, Pokolenie: 3
Najlepszy wynik: 0.31333906015429247



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 2047, Pokolenie: 1
Najlepszy wynik: 0.3714727839662142

Flow ID: 2047, Pokolenie: 2
Najlepszy wynik: 0.3714727839662142

Flow ID: 2047, Pokolenie: 3
Najlepszy wynik: 0.3714727839662142



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 2047, Pokolenie: 1
Najlepszy wynik: 0.4114572553564494

Flow ID: 2047, Pokolenie: 2
Najlepszy wynik: 0.4114572553564494

Flow ID: 2047, Pokolenie: 3
Najlepszy wynik: 0.4114572553564494



In [7]:
# main

capture = "botnet-capture-20110816-donbot"

modified_pcap_path = f"../data/interim/{capture}_perturbed.pcapng"
pcap_file_path = f'../data/raw/{capture}.pcap'
model_name = f'{capture}'

truncated_packets = create_truncated_packets_from_pcap(pcap_file_path)
truncated_packets = assign_flow_ids_to_packets(truncated_packets)
truncated_packets = undersample_flows_with_distribution(truncated_packets, 150)
optimizers = []  # Lista na instancje optymalizatorów

flow_ids = set(packet.flow_id for packet in truncated_packets)

extern = []
for flow_id in flow_ids:
    inter = []
    extern.append(inter)
    max_fitness = [0, [[0,0],0,0], 0]
    previous_max = 0
    for i in range(0, 5):
        #timing_stats = prepare_timing_stats(truncated_packets, flow_id)
        #sizing_stats = prepare_size_stats(truncated_packets,flow_id)
        #print(predict_single_flow(model_name, sizing_stats, timing_stats))
        truncated_packets_copy = copy.deepcopy(truncated_packets)
        optimizer = FlowOptimizer(truncated_packets_copy, model_name, flow_id, max_fitness[1]) 

        max_fitness = optimizer.optimize_for_flow()
        inter.append(max_fitness)
        
        #print(f'nowy: {max_fitness[1][0]} stary: {previous_max}')
        #print(max_fitness[1][0][0])
        if max_fitness[1][0][0] > previous_max: # if highest value higher than before
            
            truncated_packets = apply_best_on_packets(truncated_packets, max_fitness, flow_id)
            #print(f'size after: {prepare_size_stats(truncated_packets, flow_id)}')
            #print(f'time after: {prepare_timing_stats(truncated_packets, flow_id)}')
            
            previous_max = max_fitness[1][0][0]
        
      


modify_and_write_packets_one_by_one(pcap_file_path, modified_pcap_path, truncated_packets)

/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


[[0, 0], 0, 0]
[[0.17051189541033562, 0.03817159915492563], [{'scaling_factor': 4.172885330468564, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 4.806928159657213, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 2.058208587541895, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 2.1158464255441403, 'direction': 0.0, 'focus_point': 'middle'}], 4]
[[0.17051189541033562, 0.03817159915492563], [{'scaling_factor': 4.172885330468564, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 4.806928159657213, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 2.058208587541895, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 2.1158464255441403, 'direction': 0.0, 'focus_point': 'middle'}], 4]
[[0.17051189541033562, 0.03817159915492563], [{'scaling_factor': 4.172885330468564, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 4.806928159657213, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor'

/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


[[0.172480884501923, 0.06826299650984158], [{'scaling_factor': 3.912894924460892, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 2.983386110846609, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 2.6827393128315697, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.7149391450571296, 'direction': 1.0, 'focus_point': 'start'}], 2]
[[0.20984758654806512, 0.062326597452294186], [{'scaling_factor': 1.844353610039692, 'direction': 0.0, 'focus_point': 'end'}, {'scaling_factor': 1.3722781534863104, 'direction': 0.0, 'focus_point': 'end'}, {'scaling_factor': 1.329329309131645, 'direction': 0.0, 'focus_point': 'end'}, {'scaling_factor': 1.8979495960221682, 'direction': 0.0, 'focus_point': 'end'}], 4]
[[0.20984758654806512, 0.062326597452294186], [{'scaling_factor': 1.844353610039692, 'direction': 0.0, 'focus_point': 'end'}, {'scaling_factor': 1.3722781534863104, 'direction': 0.0, 'focus_point': 'end'}, {'scaling_factor': 1.329329309131645, 'direction': 

/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


...

[[0.20554497861702614, 0.05494246108493839], [{'scaling_factor': 2.177266650419897, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 4.875028913050298, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 2.7367343436438496, 'direction': 0.0, 'focus_point': 'middle'}, {'scaling_factor': 1.4380423634474164, 'direction': 0.0, 'focus_point': 'middle'}], 2]
[[0.25556648704429863, 0.006104225835967592], [{'scaling_factor': 2.6190241646363113, 'direction': 1.0, 'focus_point': 'end'}, {'scaling_factor': 4.271899106549247, 'direction': 1.0, 'focus_point': 'end'}, {'scaling_factor': 1.271371557485299, 'direction': 1.0, 'focus_point': 'end'}, {'scaling_factor': 2.370018516765103, 'direction': 1.0, 'focus_point': 'end'}], 2]
[[0.25556648704429863, 0.006104225835967592], [{'scaling_factor': 2.6190241646363113, 'direction': 1.0, 'focus_point': 'end'}, {'scaling_factor': 4.271899106549247, 'direction': 1.0, 'focus_point': 'end'}, {'scaling_factor': 1.271371557485299, 'directi

/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


[[0.2655294500072616, 0.00433214137667981], [{'scaling_factor': 3.2895650282620696, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 3.843943633091094, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.1402074814630467, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.1843314974907027, 'direction': 1.0, 'focus_point': 'start'}], 2]
[[0.2655294500072616, 0.00433214137667981], [{'scaling_factor': 3.2895650282620696, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 3.843943633091094, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.1402074814630467, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.1843314974907027, 'direction': 1.0, 'focus_point': 'start'}], 2]
[[0.2655294500072616, 0.00433214137667981], [{'scaling_factor': 3.2895650282620696, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 3.843943633091094, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.1402074814630467, '

/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


[[0.30457475058457706, 0.037273872071496794], [{'scaling_factor': 1.3409203782027082, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.6343055513378824, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 1.4817524584757447, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.0625021216786954, 'direction': 2.0, 'focus_point': 'start'}], 4]
[[0.30457475058457706, 0.037273872071496794], [{'scaling_factor': 1.3409203782027082, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.6343055513378824, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 1.4817524584757447, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.0625021216786954, 'direction': 2.0, 'focus_point': 'start'}], 4]
[[0.30457475058457706, 0.037273872071496794], [{'scaling_factor': 1.3409203782027082, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.6343055513378824, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 1.4817524584

In [8]:
extern[1][1][1][0][0] # TODO - i żeby tu w arrayu drugim elementem był ten drugi wynik 

0.23553400166861782

In [21]:
extern[1]

[(<pygad.pygad.GA at 0x28a4103d0>,
  [array([0.13310655]),
   [{'scaling_factor': 4.764799205222982,
     'direction': 1.0,
     'focus_point': 'start'},
    {'scaling_factor': 0.7108301292741555,
     'direction': 1.0,
     'focus_point': 'start'},
    {'scaling_factor': 1.1127549876566183,
     'direction': 1.0,
     'focus_point': 'start'},
    {'scaling_factor': 0.9474378596360743,
     'direction': 1.0,
     'focus_point': 'start'}],
   1]),
 (<pygad.pygad.GA at 0x2895b43d0>,
  [array([0.15453141]),
   [{'scaling_factor': 4.916960563476746,
     'direction': 1.0,
     'focus_point': 'start'},
    {'scaling_factor': 3.459537697813956,
     'direction': 1.0,
     'focus_point': 'start'},
    {'scaling_factor': 1.6758346777154682,
     'direction': 1.0,
     'focus_point': 'start'},
    {'scaling_factor': 1.2074639607384454,
     'direction': 1.0,
     'focus_point': 'start'}],
   2]),
 (<pygad.pygad.GA at 0x288690150>,
  [array([0.15834551]),
   [{'scaling_factor': 1.806213990120303

In [16]:
extern[2][1][1][0][0]

0.1777229868161403

In [11]:
import os
import pickle

def save_object_pickle(obj, filepath):
    """
    Saves an object to a specified filepath using pickle.
    
    Parameters:
    - obj: The object to save.
    - filepath: The path to the file where the object should be saved.
    """
    # Ensure the directory exists
    os.makedirs(os.path.dirname(filepath), exist_ok=True)
    
    with open(filepath, 'wb') as pickle_file:  # Note 'wb' for writing in binary mode
        pickle.dump(obj, pickle_file)

def load_object_pickle(filepath):
    """
    Loads an object from a specified filepath using pickle.
    
    Parameters:
    - filepath: The path to the file from which to load the object.
    
    Returns:
    - The loaded object.
    """
    with open(filepath, 'rb') as pickle_file:  # Note 'rb' for reading in binary mode
        obj = pickle.load(pickle_file)
    return obj

# Define the file path for saving. Adjust the directory as necessary.
save_object_path = f"../data/metadata/ga_rf_fitness_{capture}_perturbed.pkl"

# Save the object to a file
save_object_pickle(extern, save_object_path)

# Load the object from the file
loaded_extern = load_object_pickle(save_object_path)

print(loaded_extern)




[[(<pygad.pygad.GA object at 0x2df93d410>, [[0.172480884501923, 0.06826299650984158], [{'scaling_factor': 3.912894924460892, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 2.983386110846609, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 2.6827393128315697, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 1.7149391450571296, 'direction': 1.0, 'focus_point': 'start'}], 2]), (<pygad.pygad.GA object at 0x2f12d0590>, [[0.2120262757447995, 0.08527155455256463], [{'scaling_factor': 4.964853613002681, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 3.5817247096128826, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 2.465958596083815, 'direction': 1.0, 'focus_point': 'start'}, {'scaling_factor': 0.7742389855079054, 'direction': 1.0, 'focus_point': 'start'}], 1]), (<pygad.pygad.GA object at 0x2f2cc0650>, [[0.2399944428352302, 0.08085777980644371], [{'scaling_factor': 4.7404833085091145, 'direction': 2.0, 'focus_point': 'star

In [47]:
# Define the file path for saving. Adjust the directory as necessary.
save_object_path = f"../data/metadata/ga_rf_fitness_{capture}_perturbed.pkl"


# Load the object from the file
loaded_extern = load_object_pickle(save_object_path)

print(loaded_extern)

[[(<pygad.pygad.GA object at 0x2bb9b2110>, [[0.02322106729819018, 0.040099162522812426], [{'scaling_factor': 2.3796244739689323, 'direction': 0.0, 'focus_point': 'start'}, {'scaling_factor': 1.6362449385246731, 'direction': 0.0, 'focus_point': 'start'}, {'scaling_factor': 2.5145607696247136, 'direction': 0.0, 'focus_point': 'start'}, {'scaling_factor': 0.4420591307323537, 'direction': 0.0, 'focus_point': 'start'}], 2]), (<pygad.pygad.GA object at 0x36e4f9dd0>, [[0.04814821170684347, 0.04010634385135825], [{'scaling_factor': 3.9461210034016556, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 1.2204326649248702, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.10058073198616, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.3503679366528716, 'direction': 2.0, 'focus_point': 'start'}], 4]), (<pygad.pygad.GA object at 0x36f3e22d0>, [[0.050236094300644796, 0.21977819978723334], [{'scaling_factor': 4.027588727247559, 'direction': 2.0, 'focus_point'

In [22]:
loaded_extern[i][1][1][0][0]

0.2567169497893663

In [23]:
loaded_extern[i][1][1][0][1]

0.00240943600785426

In [49]:
# Assume loaded_extern is a structured object where you need to iterate over elements at its first index
# The goal is to access a deeply nested element, sum these values, and then calculate their average

total_sum = 0  # To accumulate the sum of elements
element_count = len(loaded_extern)  # Count of elements to iterate over

for i in range(element_count):
    # Access the deeply nested element as per the path provided
    # Assuming the path is correctly provided and represents a numeric value
    element_value = loaded_extern[i][1][1][0][1]
    total_sum += element_value  # Summing the values

# Calculating the average
# Ensure there's at least one element to avoid division by zero
if element_count > 0:
    average_value = total_sum / element_count
    print(f"Average (Accuracy): {average_value}")
else:
    print("No elements found to calculate an average.")


Average (Accuracy): 0.11874749757695113


In [30]:
# main

capture = "botnet-capture-20110816-donbot"

modified_pcap_path = f"../data/interim/{capture}_perturbed.pcapng"
pcap_file_path = f'../data/raw/{capture}.pcap'
model_name = f'{capture}'

truncated_packets = create_truncated_packets_from_pcap(pcap_file_path)
truncated_packets = assign_flow_ids_to_packets(truncated_packets)
truncated_packets = undersample_flows_with_distribution(truncated_packets, 150)
optimizers = []  # Lista na instancje optymalizatorów

flow_ids = set(packet.flow_id for packet in truncated_packets)

extern = []
for flow_id in flow_ids:
    inter = []
    extern.append(inter)
    max_fitness = [0, [[0,0],0,0], 0]
    previous_max = 0
    for i in range(0, 5):
        #timing_stats = prepare_timing_stats(truncated_packets, flow_id)
        #sizing_stats = prepare_size_stats(truncated_packets,flow_id)
        #print(predict_single_flow(model_name, sizing_stats, timing_stats))
        truncated_packets_copy = copy.deepcopy(truncated_packets)
        optimizer = FlowOptimizerTarget(truncated_packets_copy, model_name, flow_id, max_fitness[1]) 

        max_fitness = optimizer.optimize_for_flow()
        inter.append(max_fitness)
        
        #print(f'nowy: {max_fitness[1][0]} stary: {previous_max}')
        #print(max_fitness[1][0][0])
        if max_fitness[1][0][0] > previous_max: # if highest value higher than before
            
            truncated_packets = apply_best_on_packets(truncated_packets, max_fitness, flow_id)
            #print(f'size after: {prepare_size_stats(truncated_packets, flow_id)}')
            #print(f'time after: {prepare_timing_stats(truncated_packets, flow_id)}')
            
            previous_max = max_fitness[1][0][0]
        
      


modify_and_write_packets_one_by_one(pcap_file_path, modified_pcap_path, truncated_packets)

/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 2560, Pokolenie: 1
Najlepszy wynik: 0.02726001232882458

Flow ID: 2560, Pokolenie: 2
Najlepszy wynik: 0.02726001232882458

Flow ID: 2560, Pokolenie: 3
Najlepszy wynik: 0.02726001232882458



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 2560, Pokolenie: 1
Najlepszy wynik: 0.03635199550292323

Flow ID: 2560, Pokolenie: 2
Najlepszy wynik: 0.03635199550292323

Flow ID: 2560, Pokolenie: 3
Najlepszy wynik: 0.04814821170684347



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


...

Flow ID: 3575, Pokolenie: 1
Najlepszy wynik: 0.034427390121034795

Flow ID: 3575, Pokolenie: 2
Najlepszy wynik: 0.034427390121034795

Flow ID: 3575, Pokolenie: 3
Najlepszy wynik: 0.034427390121034795



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 3575, Pokolenie: 1
Najlepszy wynik: 0.021972171697053233

Flow ID: 3575, Pokolenie: 2
Najlepszy wynik: 0.021972171697053233

Flow ID: 3575, Pokolenie: 3
Najlepszy wynik: 0.021972171697053233



/Users/ppopiolek/miniconda3/envs/cyberaml/lib/python3.11/site-packages/pygad/pygad.py:1139: UserWarning: The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.
  warnings.warn("The 'delay_after_gen' parameter is deprecated starting from PyGAD 3.3.0. To delay or pause the evolution after each generation, assign a callback function/method to the 'on_generation' parameter to adds some time delay.")


Flow ID: 3575, Pokolenie: 1
Najlepszy wynik: 0.034427390121034795

Flow ID: 3575, Pokolenie: 2
Najlepszy wynik: 0.034427390121034795

Flow ID: 3575, Pokolenie: 3
Najlepszy wynik: 0.034427390121034795



In [31]:
# Save the object to a file
save_object_pickle(extern, save_object_path)

# Load the object from the file
loaded_extern = load_object_pickle(save_object_path)

print(loaded_extern)

[[(<pygad.pygad.GA object at 0x363536050>, [[0.02322106729819018, 0.040099162522812426], [{'scaling_factor': 2.3796244739689323, 'direction': 0.0, 'focus_point': 'start'}, {'scaling_factor': 1.6362449385246731, 'direction': 0.0, 'focus_point': 'start'}, {'scaling_factor': 2.5145607696247136, 'direction': 0.0, 'focus_point': 'start'}, {'scaling_factor': 0.4420591307323537, 'direction': 0.0, 'focus_point': 'start'}], 2]), (<pygad.pygad.GA object at 0x3642ce590>, [[0.04814821170684347, 0.04010634385135825], [{'scaling_factor': 3.9461210034016556, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 1.2204326649248702, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.10058073198616, 'direction': 2.0, 'focus_point': 'start'}, {'scaling_factor': 2.3503679366528716, 'direction': 2.0, 'focus_point': 'start'}], 4]), (<pygad.pygad.GA object at 0x36d3fb7d0>, [[0.050236094300644796, 0.21977819978723334], [{'scaling_factor': 4.027588727247559, 'direction': 2.0, 'focus_point'

In [54]:
def average_accuracy(loaded_extern):
    """
    Calculates the average (interpreted as accuracy) of specific elements within a nested structure.
    
    Parameters:
    - loaded_extern: A nested structured object from which values are extracted for calculation.
    
    Returns:
    - The calculated average of the extracted values, or None if the calculation cannot be performed.
    """
    total_sum = 0  # To accumulate the sum of elements
    element_count = len(loaded_extern)  # Determine the number of elements to iterate over
    
    for i in range(element_count):
        try:
            # Attempt to access the deeply nested element per the specified path
            element_value = loaded_extern[i][1][1][0][0]
            total_sum += element_value  # Summing the values
        except IndexError:
            # Handle cases where the specified path does not exist for some elements
            print(f"Warning: Could not access an element at index {i}. Skipping.")
            continue  # Skip this iteration and move to the next element
    
    # Calculate and return the average if at least one element was successfully processed
    if element_count > 0:
        return total_sum / element_count
    else:
        print("No elements found to calculate an average.")
        return None

# Example of calling the function with loaded_extern (you need to define loaded_extern according to your data structure)
# average = average_accuracy(loaded_extern)
# print(f"Average (Accuracy): {average}")


In [41]:
loaded_extern[1][1][1][0][0]

0.062070703117678594

In [55]:
average_accuracy(loaded_extern)

0.026416934861675522